# Hawaii Hazards Readiness Dashboard

In [1]:
import os, io, json
import requests, pandas as pd, geopandas as gpd, folium
from folium.plugins import MarkerCluster
from branca.element import MacroElement, Template

COUNTIES_LOCAL_PATH = r"C:\Users\micha\OneDrive\Documents\NPS\OA3802\Final Project\cb_2023_us_county_500k.zip"  # Have to manually pull due to certificate issues when pulling from Census site. 
CENTER = [20.5, -157.5]
USGS_CENTER = dict(lat=20.5, lon=-157.5, maxradiuskm=900)
RED = "#ff0000"
YELLOW = "#FFD60A"
OUT_HTML = "map.html"

In [2]:
def read_counties(p):
    g = gpd.read_file(f"zip://{p}")
    g = g[g['STATEFP']=='15']
    return g[['NAME','geometry']].to_crs(4326)

def fetch_quakes_7d_m25(center):
    end = pd.Timestamp.utcnow()
    start = end - pd.Timedelta(days=7)
    url = "https://earthquake.usgs.gov/fdsnws/event/1/query"
    q = dict(format='geojson', starttime=start.strftime('%Y-%m-%dT%H:%M:%SZ'), endtime=end.strftime('%Y-%m-%dT%H:%M:%SZ'),
             latitude=center['lat'], longitude=center['lon'], maxradiuskm=center['maxradiuskm'], minmagnitude=2.5)
    return requests.get(url, params=q, timeout=60).json()

def fetch_nws_active():
    return requests.get('https://api.weather.gov/alerts/active?area=HI', timeout=60).json()

def fetch_hnl_311():
    r = requests.get('https://data.honolulu.gov/api/views/6hui-dvrh/rows.csv?accessType=DOWNLOAD', timeout=60)
    return pd.read_csv(io.BytesIO(r.content))

def fetch_tsunami():
    url = "https://prod-histategis.opendata.arcgis.com/api/download/v1/items/437b77f132ed416294b45bde6aef23f4/geojson?layers=11"
    gdf = gpd.read_file(url).to_crs(4326)   # ensure WGS84 lat/lon
    return gdf

def quakes_to_gdf(js):
    rows = []
    for f in js['features']:
        p = f['properties']; g = f['geometry']
        if g['type']!='Point':
            continue
        lon,lat = g['coordinates'][:2]
        rows.append(dict(ts=pd.to_datetime(p['time'],unit='ms',utc=True), mag=p['mag'], lon=lon, lat=lat))
    df = pd.DataFrame(rows)
    return gpd.GeoDataFrame(df, geometry=gpd.points_from_xy(df.lon, df.lat), crs='EPSG:4326')

def clean_311_open(df):
    cols = {c.lower():c for c in df.columns}
    loc = cols.get('location')
    m = df[loc].astype(str).str.extract(r"\(?\s*(-?\d+\.?\d*)\s*,\s*(-?\d+\.?\d*)\s*\)?")
    la = pd.to_numeric(m[0]); lo = pd.to_numeric(m[1])
    cat = cols.get('requesttype')
    status_col = cols.get('statustype')
    eventdescription = cols.get('description')
    keep = pd.DataFrame({
        'cat': df[cat],
        'status': df[status_col],
        'lat': la, 'lon': lo,
        'desc': df[eventdescription]
    })
    keep = keep.dropna(subset=['lat','lon'])
    keep = keep[keep['status'].str.strip().str.casefold().isin({'received', 'submitted', 'in process','duplicate', 'on hold','referred to dept'})]
    keep['cat'] = keep['cat'].astype(str).str.strip()
    keep['desc'] = keep['desc'].str.slice(0, 200)
    return gpd.GeoDataFrame(keep, geometry=gpd.points_from_xy(keep.lon, keep.lat), crs='EPSG:4326')

def hst(ts):
    return pd.to_datetime(ts, utc=True).tz_convert('Pacific/Honolulu').strftime('%Y-%m-%d %H:%M HST')

def alerts_table_html(nws_json):
    rows = []
    for f in nws_json['features']:
        p = f['properties']
        rows.append({
            'Event': p.get('event',''),
            'Severity': p.get('severity',''),
            'Certainty': p.get('certainty',''),
            'Effective (HST)': hst(p.get('effective')),
            'Expires (HST)': hst(p.get('expires')),
            'Areas': p.get('areaDesc','')
        })
    df = pd.DataFrame(rows, columns=['Event','Severity','Certainty','Effective (HST)','Expires (HST)','Areas'])
    return df.to_html(index=False, escape=False, classes='nws-table')

In [3]:

counties = read_counties(COUNTIES_LOCAL_PATH)
tsu = fetch_tsunami()
nws = fetch_nws_active()
hnl311 = fetch_hnl_311()
q = quakes_to_gdf(fetch_quakes_7d_m25(USGS_CENTER))
g311 = clean_311_open(hnl311)
print(len(q), 'quakes |', len(g311), 'active 311HNL service requests |', len(nws['features']), 'NWS alerts')

8 quakes | 108 active 311HNL service requests | 0 NWS alerts


In [4]:
m = folium.Map(location=CENTER, zoom_start=6, control_scale=True)


folium.GeoJson(counties.to_json(), name='Counties', tooltip=folium.GeoJsonTooltip(fields=['NAME'], aliases=['County'])).add_to(m)


folium.GeoJson(tsu, name='Tsunami Zones').add_to(m)


fg_q = folium.FeatureGroup(name='Quakes (7d, M≥2.5)', show=True)
mc_q = MarkerCluster().add_to(fg_q)
for _,r in q.iterrows():
    tip = folium.Tooltip(f"{hst(r.ts)}<br>" 
                         f"{r.geometry.y:.4f}, {r.geometry.x:.4f}<br>"
                         f"M{r.mag:.1f}"
    )
    folium.CircleMarker([r.geometry.y, r.geometry.x], radius=4, color=RED, fill=True, fill_color=RED, fill_opacity=1, tooltip=tip).add_to(mc_q)
fg_q.add_to(m)


fg_3 = folium.FeatureGroup(name='Honolulu 311 — Open', show=True)
mc_3 = MarkerCluster().add_to(fg_3)
for _,r in g311.iterrows():
    tip = folium.Tooltip(f"{r.get('cat','')} — {r.get('status','')}<br>"
                         f"{r.get('desc','')}"
    )
    folium.CircleMarker([r.geometry.y, r.geometry.x], radius=4, color="#000000", fill=True, fill_color="YELLOW", fill_opacity=1, tooltip=tip).add_to(mc_3)
fg_3.add_to(m)

folium.LayerControl(collapsed=False).add_to(m)


table_html = alerts_table_html(nws)
tmpl = f"""
{{% macro html(this, kwargs) %}}
<style>
.nws-table {{ table-layout: fixed; width: 100%; }}
.nws-table td, .nws-table th {{ white-space: normal; word-break: break-word; padding: 6px 8px; border-bottom: 1px solid #e2e2e2; text-align: left; }}
.nws-table thead th {{ position: sticky; top: 0; background: #fafafa; }}
</style>
<div id='nws-panel' style='position: fixed; bottom: 12px; left: 12px; z-index: 9999; background: rgba(255,255,255,0.97); padding: 10px; border-radius: 8px; max-height: 40vh; width: 680px; overflow: auto; box-shadow: 0 2px 8px rgba(0,0,0,.2); font-family: system-ui, -apple-system, Segoe UI, Roboto, Helvetica, Arial, sans-serif; font-size: 12px;'>
  <div style='display:flex; justify-content: space-between; align-items:center; margin-bottom:6px;'>
    <strong>NWS Alerts (HI)</strong>
    <button onclick="document.getElementById('nws-panel').style.display='none';" style='border:none;background:#eee;padding:2px 6px;border-radius:4px;cursor:pointer;'>×</button>
  </div>
  {table_html}
</div>
{{% endmacro %}}
"""
panel = MacroElement(); panel._template = Template(tmpl)
m.get_root().add_child(panel)

m.save(OUT_HTML)
m